# Support vector classifier

The method of a support vector classifier is a classical machine learning classifier and meant to serve as a baseline for later comparison with the three GNNs. This classifier does not take the graph structure into account.

In [1]:
import numpy as np
import pandas as pd

import ipynb
from ipynb.fs.defs.dataset_creation import NodeClassificationDataset

import json
import os
import os.path as osp
import time

from sklearn import svm

import torch
import torch_geometric
from torch_geometric.data import Data
from torch_geometric.data import Dataset, download_url
from torch_geometric.transforms import NormalizeFeatures, RandomNodeSplit

#pd.set_option('display.max_rows', None)
#pd.set_option('display.max_columns', None)

## Define helper functions

In [2]:
def reverse(tuples):
    """
    Reverse a 2-tuple.
    """
    new_tup = tuples[::-1]
    
    return new_tup

In [3]:
def mean(dict_values):
    """
    Get mean of dictionary values.
    """
    return np.mean(np.array(list(dict_values)))

In [4]:
def std(dict_values):
    """
    Get standard deviation of dictionary values.
    """
    return np.std(np.array(list(dict_values)))

In [5]:
def filter_best_hyperparameters(df, variable):
    """
    Filter the results data frame for the best hyperparameter combination(s).
    """
    return df[df[variable] == df[variable].max()]

In [6]:
def print_best_hyperparameters(df, variable):
    """
    Print best hyperparameter combination(s).
    """
    df_best = df[df[variable] == df[variable].max()]
    print('The best hyperparameter combination/s is/are:\n\t',
          '\n\t '.join([str(df_best['parameters'].iloc[i]) for i in range(len(df_best))]),
          '\nThe resulting mean validation accuracy is:', df_best[variable].unique()[0])

## Hyperparameter tuning

We use the [scikit-learn implementation](https://scikit-learn.org/stable/modules/generated/sklearn.svm.SVC.html#sklearn.svm.SVC) of support vector classifiers `SVC` (C-Support Vector Classification). The article [In Depth: Parameter tuning for SVC](https://medium.com/all-things-ai/in-depth-parameter-tuning-for-svc-758215394769) gives a good overview of hyperparameter tuning for SVC.

With support vector classifiers, the main hyperparameters to tune are:
* `C`: regularization parameter. The strength of the regularization is inversely proportional to C. Must be strictly positive. The penalty is a squared L2 penalty. &rarr; article: C is the penalty parameter of the error term. It controls the trade-off between smooth decision boundary and classifying the training points correctly. Increasing C values may lead to overfitting the training data.
* `kernel`: specifies the kernel type to be used in the algorithm. Options are: 'linear', 'poly', 'rbf', 'sigmoid', 'precomputed'. &rarr; article: The kernel parameter selects the type of hyperplane used to separate the data. Using 'linear' will use a linear hyperplane (a line in the case of 2D data). 'rbf' and 'poly' uses a non linear hyperplane.
* `degree`: degree of the polynomial kernel function ('poly'). Ignored by all other kernels. &rarr; article: Degree is a parameter used when kernel is set to 'poly'. It is basically the degree of the polynomial used to find the hyperplane to split the data. Using degree=1 is the same as using a ‘linear’ kernel. Also, increasing this parameters leads to higher training times.
* `gamma`: kernel coefficient for 'rbf', 'poly' and 'sigmoid'. If `gamma='scale'`, which is the default, is passed, then it uses 1 / 
(n_features * X.var()) as value of gamma, if 'auto', uses 1 / n_features. &rarr; article: gamma is a parameter for non-linear hyperplanes. The higher the gamma value, the more the algorithm tries to exactly fit the training dataset.

There are still other hyperparameters that can be tuned. We do not tune them and instead rely on their default values provided in scikit-learn. We now perform the hyperparameter tuning using loops.

In [7]:
# Create results folder
route0 = "./results"

if not os.path.exists(route0):
    os.mkdir(route0)

In [9]:
start_time = time.time()

svc_results = pd.DataFrame(columns = ['parameters', 'train_accs', 'val_accs', 'test_accs', 'mean_train_acc', 'mean_val_acc', 
                                      'mean_test_acc', 'std_train_acc', 'std_val_acc', 'std_test_acc'])

seeds = [12345, 23456, 34567, 45678, 56789, 54321, 65432, 76543, 87654, 98765]

for C in [0.001, 0.01, 0.1, 1, 10, 100, 1000]:
    for kernel in ['linear', 'poly', 'rbf', 'sigmoid']:
        for degree in [0, 1, 2, 3, 4, 5, 6]: 
            for gamma in ['scale', 'auto', 0.01, 0.1, 1, 10, 100]:

                print(f'====================================================================================================\nParameter combination: {{C: {C}, kernel: {kernel}, degree: {degree}, gamma: {gamma}}}\n====================================================================================================')

                parameter_dict = dict({'C': C, 'kernel': kernel, 'degree': degree, 'gamma': gamma})

                train_acc_dict = dict() 
                val_acc_dict = dict() 
                test_acc_dict = dict() 

                for i, seed in enumerate(seeds):

                    print(f'==================================================\nRun {i+1} with seed {seed}:\n==================================================')

                    torch_geometric.seed_everything(seed)

                    dataset = NodeClassificationDataset(root='data/', transform=RandomNodeSplit(split="random", num_train_per_class = 10, num_val = 60, num_test = 129))
                    data = dataset[0]

                    # Create train, validation and test data
                    x_train = data.x[data.train_mask].numpy()
                    x_val = data.x[data.val_mask].numpy()
                    x_test = data.x[data.test_mask].numpy()

                    y_train = data.y[data.train_mask].numpy()
                    y_val = data.y[data.val_mask].numpy()
                    y_test = data.y[data.test_mask].numpy()

                    svc = svm.SVC(C=C, kernel=kernel, degree=degree, gamma=gamma) 

                    svc.fit(x_train, y_train)

                    # Get predictions on validation and test set
                    train_pred = svc.predict(x_train)
                    val_pred = svc.predict(x_val)
                    test_pred = svc.predict(x_test)

                    # Get mean accuracies
                    train_acc = svc.score(x_train, y_train)
                    val_acc = svc.score(x_val, y_val)
                    test_acc = svc.score(x_test, y_test)

                    print(f"Train mean accuracy: {train_acc} \nValidation mean accuracy: {val_acc} \nTest mean accuracy: {test_acc}")

                    train_acc_dict.update({f"{i+1}": train_acc})
                    val_acc_dict.update({f"{i+1}": val_acc})
                    test_acc_dict.update({f"{i+1}": test_acc})

                data_concat = [{'parameters': parameter_dict, 'train_accs': train_acc_dict, 'val_accs': val_acc_dict, 
                                'test_accs': test_acc_dict, 'mean_train_acc': mean(train_acc_dict.values()), 
                                'mean_val_acc': mean(val_acc_dict.values()), 'mean_test_acc': mean(test_acc_dict.values()), 
                                'std_train_acc': std(train_acc_dict.values()), 'std_val_acc': std(val_acc_dict.values()),
                                'std_test_acc': std(test_acc_dict.values())}]
                df_concat = pd.DataFrame(data_concat)
                svc_results = pd.concat([svc_results, df_concat], ignore_index=True)

print('====================================================================================================',
      '\n====================================================================================================', 
      '\n====================================================================================================')

print("saving file corresponding to svc_results.pkl")
svc_results.to_pickle(f"{route0}/svc_results.pkl")

end_time = time.time()
duration = end_time - start_time
print(f"{int(np.floor(duration/3600))} hours {(duration-3600*np.floor(duration/3600))/60:.4} minutes")

Parameter combination: {C: 0.001, kernel: linear, degree: 0, gamma: scale}
Run 1 with seed 12345:
Train mean accuracy: 0.95 
Validation mean accuracy: 0.7833333333333333 
Test mean accuracy: 0.8449612403100775
Run 2 with seed 23456:
Train mean accuracy: 0.925 
Validation mean accuracy: 0.75 
Test mean accuracy: 0.8604651162790697
Run 3 with seed 34567:
Train mean accuracy: 0.925 
Validation mean accuracy: 0.6833333333333333 
Test mean accuracy: 0.813953488372093
Run 4 with seed 45678:
Train mean accuracy: 0.925 
Validation mean accuracy: 0.8 
Test mean accuracy: 0.8294573643410853
Run 5 with seed 56789:


Processing...
Done!
Processing...
Done!
Processing...
Done!
Processing...
Done!
Processing...
Done!
Processing...
Done!
Processing...
Done!
Processing...


Train mean accuracy: 0.875 
Validation mean accuracy: 0.8166666666666667 
Test mean accuracy: 0.813953488372093
Run 6 with seed 54321:
Train mean accuracy: 0.875 
Validation mean accuracy: 0.85 
Test mean accuracy: 0.8294573643410853
Run 7 with seed 65432:
Train mean accuracy: 0.9 
Validation mean accuracy: 0.75 
Test mean accuracy: 0.875968992248062
Run 8 with seed 76543:


Done!
Processing...
Done!
Processing...
Done!


Train mean accuracy: 0.925 
Validation mean accuracy: 0.8 
Test mean accuracy: 0.8527131782945736
Run 9 with seed 87654:
Train mean accuracy: 0.95 
Validation mean accuracy: 0.8166666666666667 
Test mean accuracy: 0.7751937984496124
Run 10 with seed 98765:
Train mean accuracy: 0.9 
Validation mean accuracy: 0.85 
Test mean accuracy: 0.8294573643410853
Parameter combination: {C: 0.001, kernel: linear, degree: 0, gamma: auto}
Run 1 with seed 12345:


...

Train mean accuracy: 0.3 
Validation mean accuracy: 0.35 
Test mean accuracy: 0.32558139534883723
Run 7 with seed 65432:
Train mean accuracy: 0.275 
Validation mean accuracy: 0.43333333333333335 
Test mean accuracy: 0.43410852713178294
Run 8 with seed 76543:
Train mean accuracy: 0.275 
Validation mean accuracy: 0.35 
Test mean accuracy: 0.31007751937984496


Processing...
Done!
Processing...



Run 9 with seed 87654:
Train mean accuracy: 0.425 
Validation mean accuracy: 0.45 
Test mean accuracy: 0.37209302325581395
Run 10 with seed 98765:


Done!


Train mean accuracy: 0.325 
Validation mean accuracy: 0.5 
Test mean accuracy: 0.3953488372093023
saving file corresponding to svm_results.pkl
0 hours 39.11 minutes


In [8]:
# Look at results
svc_results = pd.read_pickle(f"{route0}/svc_results.pkl") 
svc_results

parameters  \
0     {'C': 0.001, 'kernel': 'linear', 'degree': 0, ...   
1     {'C': 0.001, 'kernel': 'linear', 'degree': 0, ...   
2     {'C': 0.001, 'kernel': 'linear', 'degree': 0, ...   
3     {'C': 0.001, 'kernel': 'linear', 'degree': 0, ...   
4     {'C': 0.001, 'kernel': 'linear', 'degree': 0, ...   
...                                                 ...   
1367  {'C': 1000, 'kernel': 'sigmoid', 'degree': 6, ...   
1368  {'C': 1000, 'kernel': 'sigmoid', 'degree': 6, ...   
1369  {'C': 1000, 'kernel': 'sigmoid', 'degree': 6, ...   
1370  {'C': 1000, 'kernel': 'sigmoid', 'degree': 6, ...   
1371  {'C': 1000, 'kernel': 'sigmoid', 'degree': 6, ...   

                                             train_accs  \
0     {'1': 0.95, '2': 0.925, '3': 0.925, '4': 0.925...   
1     {'1': 0.95, '2': 0.925, '3': 0.925, '4': 0.925...   
2     {'1': 0.95, '2': 0.925, '3': 0.925, '4': 0.925...   
3     {'1': 0.95, '2': 0.925, '3': 0.925, '4': 0.925...   
4     {'1': 0.95, '2': 0.925, '3': 0.925, '4': 0.925...   
...                                                 ...   
1367  {'1': 1.0, '2': 1.0, '3': 1.0, '4': 1.0, '5': ...   
1368  {'1': 1.0, '2': 1.0, '3': 1.0, '4': 1.0, '5': ...   
1369  {'1': 0.275, '2': 0.475, '3': 0.325, '4': 0.6,...   
1370  {'1': 0.15, '2': 0.55, '3': 0.325, '4': 0.5, '...   
1371  {'1': 0.275, '2': 0.375, '3': 0.275, '4': 0.27...   

                                               val_accs  \
0     {'1': 0.7833333333333333, '2': 0.75, '3': 0.68...   
1     {'1': 0.7833333333333333, '2': 0.75, '3': 0.68...   
2     {'1': 0.7833333333333333, '2': 0.75, '3': 0.68...   
3     {'1': 0.7833333333333333, '2': 0.75, '3': 0.68...   
4     {'1': 0.7833333333333333, '2': 0.75, '3': 0.68...   
...                                                 ...   
1367  {'1': 0.8333333333333334, '2': 0.95, '3': 0.83...   
1368  {'1': 0.8166666666666667, '2': 0.9, '3': 0.8, ...   
1369  {'1': 0.26666666666666666, '2': 0.283333333333...   
1370  {'1': 0.21666666666666667, '2': 0.366666666666...   
1371  {'1': 0.4666666666666667, '2': 0.3833333333333...   

                                              test_accs  mean_train_acc  \
0     {'1': 0.8449612403100775, '2': 0.8604651162790...          0.9150   
1     {'1': 0.8449612403100775, '2': 0.8604651162790...          0.9150   
2     {'1': 0.8449612403100775, '2': 0.8604651162790...          0.9150   
3     {'1': 0.8449612403100775, '2': 0.8604651162790...          0.9150   
4     {'1': 0.8449612403100775, '2': 0.8604651162790...          0.9150   
...                                                 ...             ...   
1367  {'1': 0.875968992248062, '2': 0.87596899224806...          0.9975   
1368  {'1': 0.8527131782945736, '2': 0.8449612403100...          0.9975   
1369  {'1': 0.23255813953488372, '2': 0.348837209302...          0.4275   
1370  {'1': 0.3023255813953488, '2': 0.5581395348837...          0.3475   
1371  {'1': 0.4186046511627907, '2': 0.4573643410852...          0.3100   

      mean_val_acc  mean_test_acc  std_train_acc  std_val_acc  std_test_acc  
0         0.790000       0.832558       0.025495     0.048419      0.026898  
1         0.790000       0.832558       0.025495     0.048419      0.026898  
2         0.790000       0.832558       0.025495     0.048419      0.026898  
3         0.790000       0.832558       0.025495     0.048419      0.026898  
4         0.790000       0.832558       0.025495     0.048419      0.026898  
...            ...            ...            ...          ...           ...  
1367      0.846667       0.863566       0.007500     0.062716      0.032742  
1368      0.825000       0.829457       0.007500     0.047288      0.053031  
1369      0.376667       0.394574       0.122704     0.094045      0.079241  
1370      0.263333       0.296899       0.114810     0.085570      0.123499  
1371      0.406667       0.382946       0.048990     0.077889      0.044827  

[1372 rows x 10 columns]

## Best hyperparameter combination

In [9]:
filter_best_hyperparameters(svc_results, 'mean_val_acc')

parameters  \
466   {'C': 0.1, 'kernel': 'poly', 'degree': 3, 'gam...   
1053  {'C': 100, 'kernel': 'poly', 'degree': 3, 'gam...   

                                             train_accs  \
466   {'1': 1.0, '2': 1.0, '3': 1.0, '4': 1.0, '5': ...   
1053  {'1': 1.0, '2': 1.0, '3': 1.0, '4': 1.0, '5': ...   

                                               val_accs  \
466   {'1': 0.8333333333333334, '2': 0.95, '3': 0.88...   
1053  {'1': 0.8333333333333334, '2': 0.95, '3': 0.88...   

                                              test_accs  mean_train_acc  \
466   {'1': 0.8914728682170543, '2': 0.8837209302325...          0.9975   
1053  {'1': 0.8914728682170543, '2': 0.8837209302325...          0.9975   

      mean_val_acc  mean_test_acc  std_train_acc  std_val_acc  std_test_acc  
466       0.876667       0.892248         0.0075     0.037417      0.021497  
1053      0.876667       0.892248         0.0075     0.037417      0.021497

In [10]:
print_best_hyperparameters(svc_results, 'mean_val_acc')

The best hyperparameter combination/s is/are:
	 {'C': 0.1, 'kernel': 'poly', 'degree': 3, 'gamma': 1}
	 {'C': 100, 'kernel': 'poly', 'degree': 3, 'gamma': 0.1} 
The resulting validation accuracy is: 0.8766666666666667


We see that there are two hyperparameter combinations that lead to the highest mean validation accuracy of 0.8767. These hyperparameter combinations differ in their respective value of `C` and `gamma`, where one has values of 0.1 and 1 and the other has values of 100 and 0.1. Apart from their equal values for the mean validation accuracy, they also display identical values for the mean training accuracy and the mean test accuracy as well as for the standard deviations of the training, validation and test accuracies. 

So, our best hyperparameter combinations are given by:

* C = 0.1
* kernel = 'poly'
* degree = 3
* gamma = 1

and 

* C = 100
* kernel = 'poly'
* degree = 3
* gamma = 0.1

They give a mean training accuracy of 0.9975, where the mean validation accuracy of 0.8767 and the mean test accuracy of 0.8922 are a little lower. The standard deviation of the training accuracies of 0.0075 is very low, where the standard deviations of the validation accuracies and the test accuracies are a bit higher, with values of 0.0374 and 0.0215, respectively.